# Determines bounding boxes for each sulcus based on a mask

This notebook determines bounding box around a sulcus. The mask is built in order to only keep sulcus of interest. <br>
It uses a supervised database, in which each sulcus has been manually labelled.

# Imports

In [76]:
import sys
import os
import json
import tempfile
import inspect
import zipfile
import dico_toolbox as dtx
import colorado as cld
import moving_averages as ma

from urllib.request import urlopen
from soma import aims

In [77]:
import anatomist.notebook as ana
a = ana.Anatomist()
print(a.headless_info.__dict__)

{'xvfb': <subprocess.Popen object at 0x7fbb085f7ba8>, 'original_display': ':1', 'display': 16, 'glx': 2, 'virtualgl': None, 'headless': True, 'mesa': False, 'qtapp': None}


The following line permits to import deep_folding even if this notebook is executed from the notebooks subfolder (and no install has been launched):

 /notebooks/use_transform.ipynb  
 /deep_folding/__init__.py

In [78]:
import deep_folding
print(inspect.getfile(deep_folding))

/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/deep_folding/__init__.py


# User-specific variables

In [79]:
sulcus = 'S.T.s.ter.asc.ant.'

In [80]:
side = 'L'

In [81]:
out_voxel_size = 1

We now assign path names and other user-specific variables.

The source directory is where the database lies. It contains the morphologist analysis subfolder ANALYSIS/3T_morphologist


In [82]:
src_dir = os.path.join(os.getcwd(), '../data/source/supervised')
src_dir = os.path.abspath(src_dir)
print(("src_dir = " + src_dir))

src_dir = /host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/source/supervised


In [83]:
bbox_dir = os.path.join(os.getcwd(), '../data/target/bbox')
bbox_dir = os.path.abspath(bbox_dir)
print(("bbox_dir = " + bbox_dir))

bbox_dir = /host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/bbox


In [84]:
mask_dir = os.path.join(os.getcwd(), '../data/target/mask')
mask_dir = os.path.abspath(mask_dir)
print(("mask_dir = " + mask_dir))

mask_dir = /host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/mask


In [85]:
ref_dir = os.path.join(os.getcwd(), '../data/reference/bbox')
ref_dir = os.path.abspath(ref_dir)
print(("ref_dir = " + ref_dir))

ref_dir = /host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/reference/bbox


In [86]:
print((sys.argv))

['/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py', '-f', '/casa/home/.local/share/jupyter/runtime/kernel-d384a570-1d0c-48af-ae70-1ed78e65e446.json']


Gets the normlized SPM file to get voxel size inside the program

norm_dir = os.path.join(os.getcwd(), '../data/source/unsupervised')
norm_dir = os.path.abspath(norm_dir)
sub_dir = "ANALYSIS/3T_morphologist/100206/t1mri/default_acquisition"

# Illustration of main program uses

### Using external calls

In [87]:
!python ../deep_folding/anatomist_tools/crop_definition.py --help

usage: mask.py [-h] [-s SRC_DIR [SRC_DIR ...]] [-t BBOX_DIR] [-m MASK_DIR]
               [-u SULCUS] [-i SIDE] [-p PATH_TO_GRAPH] [-n NB_SUBJECTS]
               [-v OUT_VOXEL_SIZE]

Computes mask and bounding box around the named sulcus

optional arguments:
  -h, --help            show this help message and exit
  -s SRC_DIR [SRC_DIR ...], --src_dir SRC_DIR [SRC_DIR ...]
                        Source directory where the MRI data lies. If there are
                        several directories, add all directories one after the
                        other. Example: -s DIR_1 DIR_2. Default is :
                        /neurospin/dico/data/bv_databases/human/pclean/all
  -t BBOX_DIR, --bbox_dir BBOX_DIR
                        Target directory where to store the output bbox json
                        files. Default is :
                        /neurospin/dico/data/deep_folding/test/bbox
  -m MASK_DIR, --mask_dir MASK_DIR
                        Target directory where to store the out

### By using the main function call

In [88]:
from deep_folding.anatomist_tools import crop_definition
print((crop_definition.__file__))

/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/deep_folding/anatomist_tools/crop_definition.py


In [89]:
args = "--help"
argv = args.split(' ')

In [90]:
crop_definition.main(argv)

usage: mask.py [-h] [-s SRC_DIR [SRC_DIR ...]] [-t BBOX_DIR] [-m MASK_DIR]
               [-u SULCUS] [-i SIDE] [-p PATH_TO_GRAPH] [-n NB_SUBJECTS]
               [-v OUT_VOXEL_SIZE]

Computes mask and bounding box around the named sulcus

optional arguments:
  -h, --help            show this help message and exit
  -s SRC_DIR [SRC_DIR ...], --src_dir SRC_DIR [SRC_DIR ...]
                        Source directory where the MRI data lies. If there are
                        several directories, add all directories one after the
                        other. Example: -s DIR_1 DIR_2. Default is :
                        /neurospin/dico/data/bv_databases/human/pclean/all
  -t BBOX_DIR, --bbox_dir BBOX_DIR
                        Target directory where to store the output bbox json
                        files. Default is :
                        /neurospin/dico/data/deep_folding/test/bbox
  -m MASK_DIR, --mask_dir MASK_DIR
                        Target directory where to store the out

### By using the API function call

In [91]:
crop_definition.bounding_box(src_dir=src_dir,
                  bbox_dir=bbox_dir,
                  mask_dir=mask_dir,
                  sulcus=sulcus,
                  side=side,
                  out_voxel_size=out_voxel_size,
                  number_subjects=0)

(0, 0, <soma.aims.Volume_FLOAT at 0x7fbaeae99828>)

# Test example

In [92]:
unsupervised_dir = os.path.join(os.getcwd(), '../data/source/unsupervised')
reference_dir = os.path.join(os.getcwd(), '../data/reference')

In [93]:
_, _, vol_mask = crop_definition.bounding_box(src_dir=src_dir,
                                    bbox_dir=bbox_dir,
                                    mask_dir=mask_dir,
                                    sulcus=sulcus,
                                    side=side,
                                    number_subjects=1,
                                    out_voxel_size=1)

{'subject': 'sujet01', 'side': 'L', 'dir': '/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/source/supervised', 'graph_file': 'sujet01/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Lsujet01*.arg'}
/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/mask/L/S.T.s.ter.asc.ant._left.nii.gz
{'subject': 'sujet01', 'side': 'L', 'dir': '/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/source/supervised', 'graph_file': 'sujet01/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Lsujet01*.arg'}
box (MNI 152) min: [129.86412145 151.36165187  60.7140839 ]
box (MNI 152) max: [154.77748948 168.99963329 107.75398868]
box (AIMS Talairach) min: [34.063088432523074, 61.7344393738619, -54.79035146878189]
box (AIMS Talairach) max: [60.66335687670315, 75.71952983264742, -4.598121985840422]
box (voxel): min =  [130 151  61]
box (voxel): max =  [155 169 108]


In [94]:
vol_mask.shape 

(193, 229, 193, 1)

In [95]:
a_vol_mask = a.toAObject(vol_mask)
axial0 = a.createWindow("Axial")
axial0.addObjects(a_vol_mask)

AnatomistInteractiveWidget(height=479, layout=Layout(height='auto', width='auto'), width=424)

In [96]:
temp_dir = tempfile.mkdtemp()
mask_filename_temp = f"{temp_dir}/mask.nii.gz"
aims.write(vol_mask, mask_filename_temp)
bucket_filename = f"{temp_dir}/mask.bck"
cmd = f"AimsFileConvert -c Bucket -t VOID -e 1 -i {mask_filename_temp} -o {bucket_filename}"
os.system(cmd)

# Displays bucket file
bucket, bucket_raw, dxyz, rot, tr = ma.load_bucket(bucket_filename)
m = dtx.convert.bucket_to_mesh(bucket)
cld.draw(m)


In [97]:
cld.draw_numpy_bucket(bucket_raw)

None


# Mask test with more than 1 subject

This takes a supervised database outside the deep_folding/data folder

In [98]:
print(mask_dir)

/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/mask


In [99]:
src_dir = "/neurospin/dico/data/bv_databases/human/pclean/all"
bbox_dir_temp = f"{temp_dir}/bbox"
mask_dir_temp = f"{temp_dir}/mask"

_, _, vol_mask = crop_definition.bounding_box(src_dir=src_dir,
                                   bbox_dir=bbox_dir_temp,
                                   mask_dir=mask_dir_temp,
                                   sulcus=sulcus,
                                   side=side,
                                   number_subjects=10,
                                   out_voxel_size=out_voxel_size)

{'subject': 'sujet01', 'side': 'L', 'dir': '/neurospin/dico/data/bv_databases/human/pclean/all', 'graph_file': 'sujet01/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Lsujet01*.arg'}
{'subject': 's12590', 'side': 'L', 'dir': '/neurospin/dico/data/bv_databases/human/pclean/all', 'graph_file': 's12590/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Ls12590*.arg'}
{'subject': 'ammon', 'side': 'L', 'dir': '/neurospin/dico/data/bv_databases/human/pclean/all', 'graph_file': 'ammon/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Lammon*.arg'}
{'subject': 'vayu', 'side': 'L', 'dir': '/neurospin/dico/data/bv_databases/human/pclean/all', 'graph_file': 'vayu/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Lvayu*.arg'}
{'subject': 'osiris', 'side': 'L', 'dir': '/neurospin/dico/data/bv_databases/human/pclean/all', 'graph_file': 'osiris/t1mri/t1/default_analysis/folds/3.3/base2018_manual/Losiris*.arg'}
{'subject': 's12919', 'side': 'L', 'dir': '/neurospin/dico/data/bv_databases/huma

In [100]:
c = aims.Converter_rc_ptr_Volume_FLOAT_BucketMap_VOID()
bucket = c(vol_mask)

In [101]:
# Displays bucket file
m = dtx.convert.bucket_to_mesh(bucket[0])
cld.draw(m)

We now represent the mask together with the MNI template:

In [102]:
# We recover the MNI template
install_dir = "."
extracted_dir = f"{install_dir}/mni_icbm152_nlin_asym_09c"
if os.path.exists(extracted_dir):
    print(f'the directory {extracted_dir} already exists. Assuming it is OK.')
else:
    dl_url = "http://www.bic.mni.mcgill.ca/~vfonov/icbm/2009/mni_icbm152_nlin_asym_09c_nifti.zip"
    tmp_dl = tempfile.mkstemp(suffix='.zip')
    with urlopen(dl_url) as f:
        with open(tmp_dl[1], 'wb') as g:
            g.write(f.read())
    # Extract the archive
    with zipfile.ZipFile(tmp_dl[1], 'r') as zf:
        zf.extractall(install_dir)

the directory ./mni_icbm152_nlin_asym_09c already exists. Assuming it is OK.


In [103]:
mni_file = f"{extracted_dir}/mni_icbm152_t1_tal_nlin_asym_09c.nii"
mni = a.loadObject(mni_file)

In [104]:
mask_vol_aims = vol_mask
print(mask_vol_aims.header())

{ 'volume_dimension' : [ 193, 229, 193, 1 ], 'sizeX' : 193, 'sizeY' : 229, 'sizeZ' : 193, 'sizeT' : 1, 'referential' : '84b1989b-eb68-8665-0049-8feaf3c22679', 'referentials' : [ 'Talairach-MNI template-SPM' ], 'transformations' : [ [ -1, 0, 0, 96, 0, -1, 0, 96, 0, 0, -1, 114, 0, 0, 0, 1 ] ], 'voxel_size' : [ 1, 1, 1, 1 ] }


In [105]:
# fusion 2D
mask_vol = a.toAObject(mask_vol_aims)
fusion2d = a.fusionObjects([mni, mask_vol], "Fusion2DMethod")
axial = a.createWindow("Axial")
axial.addObjects(fusion2d)
# params of the fusion : linear on non null
a.execute("Fusion2DParams", object=fusion2d, mode="linear_on_defined", rate=0.4)

AnatomistInteractiveWidget(height=479, layout=Layout(height='auto', width='auto'), width=424)

# Result analysis

We here compare the results with a reference result made with one subject taken from the data unsupervised source folder

Prints the list of files of the target directory

In [106]:
import os
bbox_dir_side = os.path.join(bbox_dir, side)
print(bbox_dir_side)
print(('\n'.join(os.listdir(bbox_dir_side))))

/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/bbox/L
S.T.s.ter.asc.ant._left.json


Expected output (we read the bounding_box file from the reference directory):

In [107]:
ref_dir_side = os.path.join(ref_dir, side)
ref_file = os.listdir(ref_dir_side)[0]
print("ref bbox_dir = ", ref_dir_side, '\n')
print("ref bbox_file = ", ref_file, '\n')
with open(os.path.join(ref_dir_side,ref_file), 'r') as f:
    data_ref = json.load(f)
    print((json.dumps(data_ref, sort_keys=True, indent=4)))
    box_ref = {k: data_ref[k] for k in ['bbmin_voxel', 'bbmax_voxel']}

ref bbox_dir =  /host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/reference/bbox/L 

ref bbox_file =  S.T.s.ter.asc.ant._left.json 

{
    "bbmax_AIMS_Talairach": [
        60.66335687670315,
        75.71952983264742,
        -4.598121985840422
    ],
    "bbmax_MNI152": [
        154.77748948253384,
        168.99963329321318,
        107.75398867525428
    ],
    "bbmax_voxel": [
        155,
        169,
        108
    ],
    "bbmin_AIMS_Talairach": [
        34.063088432523074,
        61.7344393738619,
        -54.79035146878189
    ],
    "bbmin_MNI152": [
        129.86412144733617,
        151.3616518724251,
        60.714083900903006
    ],
    "bbmin_voxel": [
        130,
        151,
        61
    ],
    "bbox_dir": "/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/bbox",
    "date": "2022-01-12 11:11:54",
    "git_sha": "d6adf051fa8eab17cc2be3942ad05e4e15341cb8",
    "is_git": true,
    "nb_subjects": 1,
    

Obtained output (we read the bounding_box file from the target directory):

In [108]:
bbox_file = os.listdir(bbox_dir_side)[0]
print("computed bbox_file = ", bbox_file, '\n')
with open(os.path.join(bbox_dir_side,bbox_file), 'r') as f:
    data_target = json.load(f)
    print((json.dumps(data_target, sort_keys=True, indent=4)))
    box_target = {k: data_target[k] for k in ('bbmin_voxel', 'bbmax_voxel')}

computed bbox_file =  S.T.s.ter.asc.ant._left.json 

{
    "bbmax_AIMS_Talairach": [
        60.66335687670315,
        75.71952983264742,
        -4.598121985840422
    ],
    "bbmax_MNI152": [
        154.77748948253384,
        168.99963329321318,
        107.75398867525428
    ],
    "bbmax_voxel": [
        155,
        169,
        108
    ],
    "bbmin_AIMS_Talairach": [
        34.063088432523074,
        61.7344393738619,
        -54.79035146878189
    ],
    "bbmin_MNI152": [
        129.86412144733617,
        151.3616518724251,
        60.714083900903006
    ],
    "bbmin_voxel": [
        130,
        151,
        61
    ],
    "bbox_dir": "/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/deep_folding/data/target/bbox",
    "date": "2022-01-12 15:23:23",
    "git_sha": "c505338deb528eba544d7a39c9f600494b2cf4b0",
    "is_git": true,
    "nb_subjects": 1,
    "out_voxel_size": 1,
    "repo_working_dir": "/host/volatile/jc225751/Runs/30_clean_deep_folding/Program/de

In [109]:
box_target == box_ref

True

The result shall be True. Otherwise, this means that the way in which bounding is computed has changed.